In [1]:
import os
import sys
import json
from collections import defaultdict
import ast

import numpy as np


### Training Section

In [2]:
import os
import sys
import json
from collections import defaultdict
import ast

import numpy as np
from args import args

In [3]:
import torch
import torch.optim as optim
import torch.nn as nn
import torch.nn.functional as F
import numpy as pd

from my_classes import Dataset
from random import sample
from operator import itemgetter

sys.path.append('./anaconda3/lib/python3.7/site-packages/torchvision')

from tensorboardX import SummaryWriter

writer = SummaryWriter('runs',comment="MADDPG Chessy II - mCritic Training")


# CUDA for PyTorch

use_cuda = torch.cuda.is_available()

device   = torch.device("cuda:0" if use_cuda else "cuda:1")

device_0 = torch.device("cuda:0" if use_cuda else "cpu")

device_1 = torch.device("cuda:1" if use_cuda else "cpu")

#torch.backends.cudnn.benchmark = False


max_epochs = 140000

In [4]:
import math
import random
import copy

from collections import namedtuple, deque

import torch
import torch.optim as optim
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt
import numpy as np

from args import args

def hidden_init(layer):
    fan_in = layer.weight.data.size()[0]
    lim = 1. / np.sqrt(fan_in)
    return (-lim, lim)
    
   
    
class ActorNetwork(nn.Module):
    """Actor (Policy) Model."""

    def __init__(self, state_size, action_size):

        super(ActorNetwork, self).__init__()
        self.seed = torch.manual_seed(args['seed'])
        self.fc1 = nn.Linear(state_size, args['FC1_UNITS'])
        self.fc2 = nn.Linear(args['FC1_UNITS'], args['FC2_UNITS'])
        self.fc3 = nn.Linear(args['FC2_UNITS'], args['FC3_UNITS'])
        self.fc4 = nn.Linear(args['FC3_UNITS'], action_size)

        self.reset_parameters()

    def reset_parameters(self):
        self.fc1.weight.data.uniform_(*hidden_init(self.fc1))
        self.fc2.weight.data.uniform_(*hidden_init(self.fc2))
        self.fc3.weight.data.uniform_(*hidden_init(self.fc3))
        self.fc4.weight.data.uniform_(-3e-3, 3e-3)
        
    def forward(self, state):
        """Build a network that maps state -> action values."""
        x = F.relu(self.fc1(state))
        x = F.relu(self.fc2(x))
        x = F.relu(self.fc3(x))
        return F.softmax(self.fc4(x))

    
    
class CriticNetwork(nn.Module):
    """Critic (Policy) Model."""

    def __init__(self, state_size, action_size):

        super(CriticNetwork, self).__init__()
        self.seed = torch.manual_seed(args['seed'])
        #self.fc1 = nn.Linear(state_size+action_size, args['FC1_UNITS'])
        self.fc1 = nn.Linear(state_size + action_size, args['FC1_UNITS'])
        self.fc2 = nn.Linear(args['FC1_UNITS'], args['FC2_UNITS'])
        self.fc3 = nn.Linear(args['FC2_UNITS'], args['FC3_UNITS'])
        self.fc4 = nn.Linear(args['FC3_UNITS'], 1)
        self.reset_parameters()

    def reset_parameters(self):
        self.fc1.weight.data.uniform_(*hidden_init(self.fc1))
        self.fc2.weight.data.uniform_(*hidden_init(self.fc2))
        self.fc3.weight.data.uniform_(*hidden_init(self.fc3))
        self.fc4.weight.data.uniform_(-3e-3, 3e-3)
        
    def forward(self, state, action):
        """Build a network that maps state -> action values."""
        #state_action = torch.cat((state, action),dim=1)
        #print("STATE_ACTION.shape:\t{}".format(state_action.shape))
        x = F.relu(self.fc1(torch.cat((state, action), dim=1)))
        x = F.relu(self.fc2(x))
        x = F.relu(self.fc3(x))
        return self.fc4(x)
   
class Actor():
    """Interacts with and learns from the environment."""

    def __init__(self, state_size, action_size):

        #self.state_action_size   = state_action_size
        self.seed         = args['seed']
        self.device       = device_1
    
        self.network    = ActorNetwork(state_size, action_size).to(self.device)
        self.target     = ActorNetwork(state_size, action_size).to(self.device)
        self.optimizer  = optim.Adam(self.network.parameters(), lr=args['LR_ACTOR'])
    
class MCritic():
    """Interacts with and learns from the environment."""

    def __init__(self, state_size, action_size):

        #self.state_action_size   = state_action_size
        self.seed         = args['seed']
        self.device       = device_0

        self.network      = CriticNetwork(state_size, action_size).to(self.device)
        self.target       = CriticNetwork(state_size, action_size).to(self.device)
        self.optimizer    = optim.Adam(self.network.parameters(), lr=args['LR_CRITIC'], weight_decay=args['WEIGHT_DECAY'])
        
        #Model takes too long to run --> load model weights from previous run (took > 24hours on my machine)
        #self.network.load_state_dict(torch.load(args['mcritic_path']), strict=False)
        #self.target.load_state_dict(torch.load(args['mcritic_path']), strict=False)

### Setup for Batch Training

#### Get total number of batch files 

In [5]:
import os
import random

In [6]:
data_dir = "/data_data/reinforcement_learning/results/model_splits/"
batch_files = os.listdir(data_dir)
batch_files[:10]

['x99953938.tsv',
 'x9999024391.tsv',
 'x9999021282.tsv',
 'x9999001244.tsv',
 'x99926665.tsv',
 'x9999035688.tsv',
 'x99914598.tsv',
 'x99905123.tsv',
 'x99960980.tsv',
 'x99948602.tsv']

In [7]:
batch_IDs = [x.split(".")[0][1:].strip() for x in batch_files]
batch_IDs[:5]

['99953938', '9999024391', '9999021282', '9999001244', '99926665']

In [8]:
batch_IDs_shuffled = random.sample(batch_IDs, len(batch_IDs))
batch_IDs_shuffled[-10:]

['99968829',
 '99919161',
 '99936113',
 '9999030248',
 '99984488',
 '99987737',
 '9999000980',
 '9999022425',
 '99952652',
 '99973092']

### Train MCritic

In [9]:
from sparse_action_dict import sparse_action_dict
from numeric_names import numeric_names

In [10]:
train_pctl       = 0.65
validation_pctl  = 0.80
test_pctl        = 0.20

In [11]:
num_policies     = len(batch_IDs_shuffled)
train_cut_pt     = int(train_pctl*num_policies)
val_cut_pt       = int(validation_pctl*num_policies)

In [12]:
partition_ = {}
partition_['train']      = []
partition_['validation'] = []
parts = ['train','validation']

In [13]:
train_cut_pt       = int(train_pctl*num_policies)
val_cut_pt         = int(validation_pctl*num_policies)
training_generator = None

In [14]:
train_idxs = batch_IDs_shuffled[:train_cut_pt]
val_idxs   = batch_IDs_shuffled[train_cut_pt:val_cut_pt]
test_idxs  = batch_IDs_shuffled[val_cut_pt:]

In [15]:
null_action_vect   = np.zeros(args['action_size'])
print(null_action_vect)
action_sparse_dict = {str([int(x) for x in v]):args['action_id_dict'][k] for k,v in sparse_action_dict.items()}
action_sparse_dict

for state_action in action_sparse_dict:
    null_action_vect   = np.zeros(args['action_size'])
    null_action_vect[action_sparse_dict[state_action]] = 1
    action_sparse_dict[state_action] = null_action_vect
    
str(list(action_sparse_dict.values())[-1:][0])

[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


'[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.\n 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.\n 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.\n 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1.]'

In [16]:
training_generator = None
state_batch = None
action_batch = None
labels_batch = None

In [17]:
def one_hot_encode(batch,depth):
    ones = torch.sparse.torch.eye(depth).to(device)
    return ones.index_select(0,batch).to(device)

In [18]:
def load_batch_file(idx):
    
    #print("load_batch_file: \t{}".format(idx))
    
    if int(idx) < 10:
        
        file = os.path.join(data_dir, "x" + str(idx) + ".tsv")
    else:
        file = os.path.join(data_dir, "x" + str(idx) + ".tsv")
        
    return np.loadtxt(fname=file,dtype=np.str, delimiter="\t")

In [19]:
def getModelLoss(idx,model):
    
    #print('get_data_and_labels...:\t{}'.format(idx))
    
    device   = torch.device("cuda:0" if use_cuda else "cpu")
    
    if model == mCritic:
        device   = torch.device("cuda:0" if use_cuda else "cpu")
    else:
        device   = torch.device("cuda:1" if use_cuda else "cpu")
    
    global labels_batch
    global state_batch
    global action_batch
    
    batch_file_df = load_batch_file(idx)
    
    state   = torch.tensor([ast.literal_eval(x)[:args['state_size']] for x in batch_file_df[:,0]]).float().to(device)
    
    _action_ = [ast.literal_eval(x)[args['state_size']:] for x in batch_file_df[:,0]]
    
    action_  = [str(action_sparse_dict[str(x).replace("\n","").strip()]).replace(" ",",") for x in _action_]
    
    action  = torch.tensor([ast.literal_eval(x) for x in action_]).float().to(device)
    
    labels  = torch.tensor([ast.literal_eval(x) for x in batch_file_df[:,1]]).float().to(device)
    
    state_batch  = state.to(device)
        
    action_batch = action.to(device)
        
    labels_batch = labels.view(args['BATCH_SIZE'],-1).to(device)
    
    if model == mCritic:
        
        Q_targets  = labels_batch

        Q_expected = model.network(state_batch, action_batch)
        
        loss = F.mse_loss(Q_expected, Q_targets)
        
        return loss
        
    else:
        
        mid_point   = int((args['action_size'])/2)
        
        Q_targets   = torch.argmax(action_batch[:,:mid_point], dim=1)
        
        Q_expected  = torch.argmax(model.network(state_batch)[:,:mid_point], dim=1)
        
        #Q_expected  = one_hot_encode(best_action.reshape(-1),mid_point)
        
        loss        = F.l1_loss(Q_expected.float(), Q_targets.float())
        
        loss.requires_grad = True
    
        return loss
        
    

In [20]:
import psutil

epoch = 0
num_cpus = psutil.cpu_count(logical=False) - 2 
print("Using {} CPUs".format(num_cpus))

Using 8 CPUs


In [21]:
import sys

def train_epoch(epoch):    
    
    for model in [actor]:

        # Training
        train_idx  = sample(train_idxs, 1)[0]
        model_loss = getModelLoss(train_idx,model)

        # Minimize the loss
        model.optimizer.zero_grad()
        model_loss.backward()
        model.optimizer.step()

        # Validation
        with torch.set_grad_enabled(False):
            val_idx     = sample(val_idxs, 1)[0]   
            model_val_loss = getModelLoss(val_idx,model)


        if epoch % 1 == 0 and epoch > 0:
            num_iter = epoch
            if model == mCritic:
                writer.add_scalars('mCritic_loss_II', {
                    'mCritic_train_loss': model_loss, 
                    'mCritic_val_loss': model_val_loss,
                },  epoch)
                print("Epoch:\t{}\tmCritic_train_mse_loss:\t{}\tmCritic_val_mse_loss:\t{}".format(epoch,model_loss, model_val_loss))
            else:
                writer.add_scalars('Actor_loss_II', {
                    'Actor_train_loss': model_loss, 
                    'Actor_val_loss': model_val_loss,
                },  epoch)
                print("Epoch:\t{}\tActor_train_L1_loss:\t{}\tActor_val_L1_loss:\t{}".format(epoch,model_loss, model_val_loss))

        
        

            

In [22]:
def train():
    
    for epoch in range(max_epochs):
        
        train_epoch(epoch)

In [23]:
if __name__ == '__main__':
    
    mCritic =  MCritic(args['state_size'], args['action_size'])
    
    actor   =  Actor(args['state_size'], args['action_size'])
    
    train()
    #pass

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:48: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


Epoch:	1	Actor_train_L1_loss:	20.91015625	Actor_val_L1_loss:	19.8974609375
Epoch:	2	Actor_train_L1_loss:	19.640625	Actor_val_L1_loss:	20.349609375
Epoch:	3	Actor_train_L1_loss:	19.923828125	Actor_val_L1_loss:	19.63671875
Epoch:	4	Actor_train_L1_loss:	20.240234375	Actor_val_L1_loss:	19.4775390625
Epoch:	5	Actor_train_L1_loss:	19.65625	Actor_val_L1_loss:	20.345703125
Epoch:	6	Actor_train_L1_loss:	20.0849609375	Actor_val_L1_loss:	20.52734375
Epoch:	7	Actor_train_L1_loss:	19.7880859375	Actor_val_L1_loss:	20.3056640625
Epoch:	8	Actor_train_L1_loss:	20.5087890625	Actor_val_L1_loss:	20.046875
Epoch:	9	Actor_train_L1_loss:	20.2021484375	Actor_val_L1_loss:	19.7353515625
Epoch:	10	Actor_train_L1_loss:	19.939453125	Actor_val_L1_loss:	20.3232421875
Epoch:	11	Actor_train_L1_loss:	19.05859375	Actor_val_L1_loss:	20.88671875
Epoch:	12	Actor_train_L1_loss:	19.76171875	Actor_val_L1_loss:	20.3203125
Epoch:	13	Actor_train_L1_loss:	19.8427734375	Actor_val_L1_loss:	19.9404296875
Epoch:	14	Actor_train_L1_los

Epoch:	109	Actor_train_L1_loss:	20.26953125	Actor_val_L1_loss:	20.171875
Epoch:	110	Actor_train_L1_loss:	20.146484375	Actor_val_L1_loss:	20.234375
Epoch:	111	Actor_train_L1_loss:	20.244140625	Actor_val_L1_loss:	20.298828125
Epoch:	112	Actor_train_L1_loss:	20.76953125	Actor_val_L1_loss:	20.4189453125
Epoch:	113	Actor_train_L1_loss:	19.8720703125	Actor_val_L1_loss:	20.1318359375
Epoch:	114	Actor_train_L1_loss:	19.998046875	Actor_val_L1_loss:	19.376953125
Epoch:	115	Actor_train_L1_loss:	19.3095703125	Actor_val_L1_loss:	19.962890625
Epoch:	116	Actor_train_L1_loss:	20.4111328125	Actor_val_L1_loss:	19.8876953125
Epoch:	117	Actor_train_L1_loss:	20.2109375	Actor_val_L1_loss:	20.779296875
Epoch:	118	Actor_train_L1_loss:	19.8447265625	Actor_val_L1_loss:	20.0654296875
Epoch:	119	Actor_train_L1_loss:	20.544921875	Actor_val_L1_loss:	19.5732421875
Epoch:	120	Actor_train_L1_loss:	20.603515625	Actor_val_L1_loss:	20.2890625
Epoch:	121	Actor_train_L1_loss:	19.654296875	Actor_val_L1_loss:	19.9033203125
E

Epoch:	216	Actor_train_L1_loss:	19.7568359375	Actor_val_L1_loss:	20.482421875
Epoch:	217	Actor_train_L1_loss:	19.96484375	Actor_val_L1_loss:	19.4267578125
Epoch:	218	Actor_train_L1_loss:	20.4697265625	Actor_val_L1_loss:	20.2744140625
Epoch:	219	Actor_train_L1_loss:	20.330078125	Actor_val_L1_loss:	20.3291015625
Epoch:	220	Actor_train_L1_loss:	19.8154296875	Actor_val_L1_loss:	19.244140625
Epoch:	221	Actor_train_L1_loss:	20.0244140625	Actor_val_L1_loss:	20.1787109375
Epoch:	222	Actor_train_L1_loss:	19.9208984375	Actor_val_L1_loss:	19.16015625
Epoch:	223	Actor_train_L1_loss:	20.4951171875	Actor_val_L1_loss:	19.99609375
Epoch:	224	Actor_train_L1_loss:	19.7314453125	Actor_val_L1_loss:	20.4638671875
Epoch:	225	Actor_train_L1_loss:	19.8232421875	Actor_val_L1_loss:	19.3251953125
Epoch:	226	Actor_train_L1_loss:	20.142578125	Actor_val_L1_loss:	19.4677734375
Epoch:	227	Actor_train_L1_loss:	20.2880859375	Actor_val_L1_loss:	20.40234375
Epoch:	228	Actor_train_L1_loss:	20.6484375	Actor_val_L1_loss:	20

Epoch:	323	Actor_train_L1_loss:	19.2646484375	Actor_val_L1_loss:	19.52734375
Epoch:	324	Actor_train_L1_loss:	19.888671875	Actor_val_L1_loss:	19.6796875
Epoch:	325	Actor_train_L1_loss:	19.7705078125	Actor_val_L1_loss:	20.0732421875
Epoch:	326	Actor_train_L1_loss:	21.2607421875	Actor_val_L1_loss:	20.6923828125
Epoch:	327	Actor_train_L1_loss:	19.5634765625	Actor_val_L1_loss:	20.0634765625
Epoch:	328	Actor_train_L1_loss:	19.712890625	Actor_val_L1_loss:	19.666015625
Epoch:	329	Actor_train_L1_loss:	20.27734375	Actor_val_L1_loss:	20.51171875
Epoch:	330	Actor_train_L1_loss:	19.69921875	Actor_val_L1_loss:	19.8779296875
Epoch:	331	Actor_train_L1_loss:	20.087890625	Actor_val_L1_loss:	19.724609375
Epoch:	332	Actor_train_L1_loss:	20.7021484375	Actor_val_L1_loss:	19.9775390625
Epoch:	333	Actor_train_L1_loss:	19.6669921875	Actor_val_L1_loss:	18.8935546875
Epoch:	334	Actor_train_L1_loss:	19.6279296875	Actor_val_L1_loss:	19.4521484375
Epoch:	335	Actor_train_L1_loss:	20.4599609375	Actor_val_L1_loss:	20.

...

Epoch:	87393	Actor_train_L1_loss:	19.7470703125	Actor_val_L1_loss:	19.798828125
Epoch:	87394	Actor_train_L1_loss:	20.5927734375	Actor_val_L1_loss:	20.3876953125
Epoch:	87395	Actor_train_L1_loss:	20.572265625	Actor_val_L1_loss:	19.5546875
Epoch:	87396	Actor_train_L1_loss:	19.8984375	Actor_val_L1_loss:	19.7958984375
Epoch:	87397	Actor_train_L1_loss:	19.916015625	Actor_val_L1_loss:	20.326171875
Epoch:	87398	Actor_train_L1_loss:	19.9072265625	Actor_val_L1_loss:	19.833984375
Epoch:	87399	Actor_train_L1_loss:	20.2822265625	Actor_val_L1_loss:	19.9423828125
Epoch:	87400	Actor_train_L1_loss:	19.87109375	Actor_val_L1_loss:	19.1484375
Epoch:	87401	Actor_train_L1_loss:	20.26953125	Actor_val_L1_loss:	19.9931640625
Epoch:	87402	Actor_train_L1_loss:	20.451171875	Actor_val_L1_loss:	20.2734375
Epoch:	87403	Actor_train_L1_loss:	19.650390625	Actor_val_L1_loss:	19.22265625
Epoch:	87404	Actor_train_L1_loss:	20.5078125	Actor_val_L1_loss:	20.2607421875
Epoch:	87405	Actor_train_L1_loss:	20.0205078125	Actor_va

Epoch:	87497	Actor_train_L1_loss:	20.2607421875	Actor_val_L1_loss:	20.599609375
Epoch:	87498	Actor_train_L1_loss:	20.052734375	Actor_val_L1_loss:	20.4052734375
Epoch:	87499	Actor_train_L1_loss:	19.8017578125	Actor_val_L1_loss:	20.607421875
Epoch:	87500	Actor_train_L1_loss:	19.4423828125	Actor_val_L1_loss:	19.7802734375
Epoch:	87501	Actor_train_L1_loss:	20.2841796875	Actor_val_L1_loss:	19.4775390625
Epoch:	87502	Actor_train_L1_loss:	19.71484375	Actor_val_L1_loss:	20.2841796875
Epoch:	87503	Actor_train_L1_loss:	19.80859375	Actor_val_L1_loss:	20.0576171875
Epoch:	87504	Actor_train_L1_loss:	20.2890625	Actor_val_L1_loss:	20.12109375
Epoch:	87505	Actor_train_L1_loss:	19.3701171875	Actor_val_L1_loss:	20.119140625
Epoch:	87506	Actor_train_L1_loss:	19.353515625	Actor_val_L1_loss:	21.2236328125
Epoch:	87507	Actor_train_L1_loss:	20.3740234375	Actor_val_L1_loss:	19.859375
Epoch:	87508	Actor_train_L1_loss:	20.0107421875	Actor_val_L1_loss:	20.083984375
Epoch:	87509	Actor_train_L1_loss:	20.0009765625

Epoch:	87601	Actor_train_L1_loss:	20.15625	Actor_val_L1_loss:	20.2197265625
Epoch:	87602	Actor_train_L1_loss:	19.8076171875	Actor_val_L1_loss:	19.8056640625
Epoch:	87603	Actor_train_L1_loss:	19.4482421875	Actor_val_L1_loss:	20.185546875
Epoch:	87604	Actor_train_L1_loss:	20.47265625	Actor_val_L1_loss:	20.6728515625
Epoch:	87605	Actor_train_L1_loss:	20.0615234375	Actor_val_L1_loss:	19.6123046875
Epoch:	87606	Actor_train_L1_loss:	20.525390625	Actor_val_L1_loss:	19.9462890625
Epoch:	87607	Actor_train_L1_loss:	19.984375	Actor_val_L1_loss:	19.7421875
Epoch:	87608	Actor_train_L1_loss:	19.6728515625	Actor_val_L1_loss:	20.3291015625
Epoch:	87609	Actor_train_L1_loss:	20.26953125	Actor_val_L1_loss:	20.4609375
Epoch:	87610	Actor_train_L1_loss:	20.9052734375	Actor_val_L1_loss:	20.1142578125
Epoch:	87611	Actor_train_L1_loss:	19.7958984375	Actor_val_L1_loss:	20.236328125
Epoch:	87612	Actor_train_L1_loss:	20.8466796875	Actor_val_L1_loss:	19.8896484375
Epoch:	87613	Actor_train_L1_loss:	20.1083984375	Ac

Epoch:	87705	Actor_train_L1_loss:	19.5234375	Actor_val_L1_loss:	19.8232421875
Epoch:	87706	Actor_train_L1_loss:	20.072265625	Actor_val_L1_loss:	19.9345703125
Epoch:	87707	Actor_train_L1_loss:	20.4892578125	Actor_val_L1_loss:	19.7607421875
Epoch:	87708	Actor_train_L1_loss:	19.8701171875	Actor_val_L1_loss:	19.4111328125
Epoch:	87709	Actor_train_L1_loss:	20.0927734375	Actor_val_L1_loss:	20.3525390625
Epoch:	87710	Actor_train_L1_loss:	21.001953125	Actor_val_L1_loss:	20.181640625
Epoch:	87711	Actor_train_L1_loss:	20.0576171875	Actor_val_L1_loss:	20.27734375
Epoch:	87712	Actor_train_L1_loss:	20.2373046875	Actor_val_L1_loss:	19.2900390625
Epoch:	87713	Actor_train_L1_loss:	20.2958984375	Actor_val_L1_loss:	19.7392578125


KeyboardInterrupt: 

In [ ]:
torch.save(mCritic.network.state_dict(), '/data_data/reinforcement_learning/results/checkpoint_actor_09202020_L1_Loss_TBD.pth')

## Use Multiprocessing to speed up training

In [ ]:
import torch.multiprocessing as mp


if __name__ == '__main__':
    
    
    mCritic =  MCritic(args['state_size'], args['action_size'])
    
    mp.set_start_method('spawn', force=True)
    
    mCritic.network.share_memory()
    
    processes = []
    
    for i in range(10):
        
        p = mp.Process(target=train, args=(mCritic,))
        
        p.start()
        
        processes.append(p)
    
    for p in processes:
        
        p.join()